In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import StructType, StructField, ArrayType, IntegerType, FloatType, StringType, BooleanType

# log2 file
log2 = spark.read.csv('/FileStore/tables/log2.csv', header='false')
# Product Categories 
prod_cat = spark.read.csv('/FileStore/tables/product_categories.csv', header='true')
# Products
prod = spark.read.csv('/FileStore/tables/products.csv', header='true')

# Data Pre-Processing

In [0]:
log_df = log2.withColumnRenamed("_c0", "sentiment") \
            .withColumnRenamed("_c1", "publication_url") \
            .withColumnRenamed("_c2", "product_url") \
            .withColumnRenamed("_c3", "click") \
            .withColumnRenamed("_c4", "gender") \
            .withColumnRenamed("_c5", "age_group")
log_df.show(truncate=False)

+---------+-------------------------------+------------------------------+-----+----------+----------+
|sentiment|publication_url                |product_url                   |click|gender    |age_group |
+---------+-------------------------------+------------------------------+-----+----------+----------+
|positive |https://www.foxnews.com/       |https://lees.com/jeans        |0    |female    |juvenile  |
|neutral  |https://www.mirror.co.uk/news/ |https://coach.com/purses      |0    |male      |young     |
|negative |https://www.nbcnews.com/       |https://covergirl.co/lipsticks|0    |male      |middle-age|
|positive |https://www.examiner.com/      |https://covergirl.co/makeup   |0    |non-binary|juvenile  |
|negative |https://www.nj.com             |https://dell.com/computers    |1    |female    |young     |
|positive |https://www.chicagotribune.com/|https://remington.com/shavers |1    |male      |senior    |
|negative |https://www.msn.com/en-us/news |https://dell.com/laptops      

In [0]:
prod_cat = prod_cat.withColumn('category', trim(prod_cat.category))
prod_cat = prod_cat.withColumn('product', trim(prod_cat.product))
prod_cat.show(truncate=False) 

+------------------+------------------------+
|product           |category                |
+------------------+------------------------+
|blender           |small kitchen appliances|
|pressure cooker   |small kitchen appliances|
|computer          |consumer electronics    |
|coffee            |packaged food           |
|vitamin           |health                  |
|treadmill         |fitness equipment       |
|face cream        |beauty products         |
|rowing machine    |fitness equipment       |
|elliptical trainer|fitness equipment       |
|lipstick          |beauty products         |
|women's purse     |accessories             |
|shoes             |footwear                |
|car               |transportation          |
|jeans             |apparel                 |
|television        |consumer electronics    |
|tablet            |consumer electronics    |
|furniture         |household durables      |
|washer            |large kitchen appliances|
|dryer             |large kitchen 

In [0]:
prod = prod.withColumn('product', trim(prod.product))
prod = prod.withColumn('product_url', trim(prod.product_URL)) 
prod = prod.withColumn('product_type', trim(prod.product_type)) 
prod.show(truncate=False) 

+--------------------------+----------------------------------+------------------+
|product                   |product_url                       |product_type      |
+--------------------------+----------------------------------+------------------+
|Vitamix blender           |https://vitamix.com/blenders      |blender           |
|Lenova laptop             |https://lenova.com/laptops        |computer          |
|InstantPot pressure cooker|https://InstantPot.com/cookers    |pressure cooker   |
|NemoK blender             |http://nemoK.co/blenders          |blender           |
|Hamilton Beach blender    |https://HamiltonBeach.com/blenders|blender           |
|Lavazza Coffee            |https://Lavazza.com/coffee        |coffee            |
|Starbucks Coffee          |https://Starbucks.com/coffee      |coffee            |
|Centrum MultiVitamins     |https://centrum.com/vitamins      |vitamin           |
|NordicTrack treadmill     |https://NordicTrack.com/treadmills|treadmill         |
|Nor

In [0]:
print("Log 2 df = ", (log_df.count(), len(log_df.columns)))
print("Products df = ", (prod.count(), len(prod.columns)))
print("Product Categories df = ",  (prod_cat.count(), len(prod_cat.columns)))

Log 2 df =  (10000, 6)
Products df =  (51, 3)
Product Categories df =  (25, 2)


In [0]:
# 1. For each product, compute all the Publication_URLs containing an ad for that product.
import re
@udf(returnType=BooleanType())
def match_re(url1, url2):
    # Check for exact equality 
    if url1 == url2:
        return True
    # Search for patterns in both URLs
    match1 = re.compile(r'^https?://([\w]+)(?:\.com)?/([\w]+)$',re.IGNORECASE).search(url1)
    match2 = re.compile(r'^https?://([\w]+)(?:\.com)?/([\w]+)$',re.IGNORECASE).search(url2)
    if match1 and match2:
        group1_equal = match1.group(1) == match2.group(1)
        group2_equal = match1.group(2) == match2.group(2)
        return group1_equal and group2_equal
    # If no match or groups are not equal, return False 
    return False

# Creating a single Dataframe

In [0]:
prod_log_df = prod.crossJoin(log_df).where(match_re(prod.product_url, log_df.product_url))
prod_log_cat = prod_log_df.join(prod_cat, on=prod.product_type==prod_cat.product, how='outer')
prod_log_cat = prod_log_cat.select(prod.product, prod.product_url, prod.product_type, 
                                log_df.sentiment, log_df.publication_url, log_df.click, log_df.gender, log_df.age_group,
                                prod_cat.category)
prod_log_cat.display()

product product_url product_type sentiment publication_url click gender age_group category Vitamix blender https://vitamix.com/blenders blender positive https://www.bostonglobe.com/ 1 female senior small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.sfgate.com/ 0 male juvenile small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender neutral https://nypost.com/ 0 female senior small kitchen appliances Vitamix blender https://vitamix.com/blenders blender negative https://abcnews.go.com/ 0 female juvenile small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.dailymail.co.uk/ 1 female senior small kitchen appliances Vitamix blender https://vitamix.com/blenders blender positive https://www.latimes.com/ 1 male senior small kitchen appliances NemoK blender http://nemoK.co/blenders blender negative https://mashable.com/ 1 male senior small kitchen appliances NemoK blender http://nemoK.co/blenders blender positive https://mashable.com/ 1 male senior small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.sfgate.com/ 0 male young small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.sfgate.com/ 0 female middle-age small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.npr.org/ 1 female young small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.npr.org/ 0 female senior small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.cbsnews.com/ 1 female young small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender neutral https://www.foxnews.com/ 1 female senior small kitchen appliances Vitamix blender https://vitamix.com/blenders blender positive https://abcnews.go.com/ 1 female young small kitchen appliances Vitamix blender https://vitamix.com/blenders blender negative https://www.al.com/ 1 male juvenile small kitchen appliances Vitamix blender https://vitamix.com/blenders blender positive https://www.al.com/ 0 male juvenile small kitchen appliances NemoK blender http://nemoK.co/blenders blender positive https://www.usnews.com/ 0 female young small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.sfgate.com/ 0 female senior small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender positive https://www.nbcnews.com/ 0 female middle-age small kitchen appliances NemoK blender http://nemoK.co/blenders blender negative https://www.cnn.com/ 1 female middle-age small kitchen appliances NemoK blender http://nemoK.co/blenders blender negative https://www.boston.com 1 male young small kitchen appliances NemoK blender http://nemoK.co/blenders blender positive https://www.examiner.com/ 1 female young small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender neutral https://techcrunch.com/ 0 female senior small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender negative https://www.telegraph.co.uk/ 1 male senior small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender neutral https://www.theatlantic.com/ 0 female juvenile small kitchen appliances Vitamix blender https://vitamix.com/blenders blender positive https://www.dallasnews.com/ 0 male juvenile small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender positive https://www.foxnews.com/ 0 male middle-age small kitchen appliances NemoK blender http://nemoK.co/blenders blender neutral https://www.cbsnews.com/ 1 male senior small kitchen appliances Hamilton Beach blender https://HamiltonBeach.com/blenders blender positive https://www.foxnews.com/ 0 male juvenile small kitchen appliances Vitamix blender https://vitamix.com/blenders blender negative https://time.com/ 1 female middl

### 1. For each product, compute all the Publication_URLs containing an ad for that product. 

In [0]:
result = prod_log_cat.select('product', 'publication_url').filter(prod_log_cat.product.isNotNull())
result = result.groupBy("product").agg(count('publication_url').alias('count'), collect_list('publication_url').alias('Publication_URLs'))
result = result.orderBy(desc('count'))
result.display() 

product count Publication_URLs Dell laptop 698 List(https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.businessinsider.com/, https://www.businessinsider.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.huffingtonpost.com/, https://www.huffingtonpost.com/, https://www.nydailynews.com/, https://www.nydailynews.com/, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.usnews.com/, https://www.usnews.com/, https://techcrunch.com/, https://techcrunch.com/, https://www.buzzfeed.com/, https://www.buzzfeed.com/, https://www.bostonglobe.com/, https://www.bostonglobe.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.buzzfeed.com/, https://www.buzzfeed.com/, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.dallasnews.com/, https://www.dallasnews.com/, https://www.thedailybeast.com/, https://www.thedailybeast.com/, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.telegraph.co.uk/, https://www.telegraph.co.uk/, https://www.boston.com, https://www.boston.com, https://www.bostonglobe.com/, https://www.bostonglobe.com/, https://www.examiner.com/, https://www.examiner.com/, https://techcrunch.com/, https://techcrunch.com/, https://www.thedailybeast.com/, https://www.thedailybeast.com/, https://techcrunch.com/, https://techcrunch.com/, https://www.buzzfeed.com/, https://www.buzzfeed.com/, https://www.bostonglobe.com/, https://www.bostonglobe.com/, https://www.businessinsider.com/, https://www.businessinsider.com/, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.huffingtonpost.com/, https://www.huffingtonpost.com/, https://www.nj.com, https://www.nj.com, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.telegraph.co.uk/, https://www.telegraph.co.uk/, https://www.examiner.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.telegraph.co.uk/, https://www.telegraph.co.uk/, https://www.thedailybeast.com/, https://www.thedailybeast.com/, https://www.vice.com/en_us, https://www.vice.com/en_us, https://www.telegraph.co.uk/, https://www.telegraph.co.uk/, https://www.boston.com, https://www.boston.com, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.examiner.com/, https://www.examiner.com/, https://www.nj.com, https://www.nj.com, https://www.thedailybeast.com/, https://www.thedailybeast.com/, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.nbcnews.com/, https://www.nbcnews.com/, https://www.usnews.com/, https://www.usnews.com/, https://www.chicagotribune.com/, https://www.chicagotribune.com/, https://www.businessinsider.com/, https://www.businessinsider.com/, https://www.vice.com/en_us, https://www.vice.com/en_us, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.usatoday.com/, https://www.usatoday.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.businessinsider.com/, https://www.businessinsider.com/, https://www.usnews.com/, https://www.usnews.com/, https://www.huffingtonpost.com/, https://www.huffingtonpost.com/, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.bostonglobe.com/, https://www.bostonglobe.com/, https://www.thedailybeast.com/, https://www.thedailybeast.com/, https://www.telegraph.co.uk/, https://www.telegraph.co.uk/, https://www.chicagotribune.com/, https://www.chicagotribune.com/, https://www.usnews.com/, https://www.usnews.com/, https://www.buzzfeed.com/, https://www.buzzfeed.com/, https://www.nbcnews.com/, https://www.nbcnews.com/, https://www.usatoday.com/, https://www.usatoday.com/, https://www.vice.com/en_us, https://www.vice.com/en_us, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.dallasnews.com/, https://www.dallasnews.com/, https:

### 2. For each product type, compute all the Publication_URLs containing an ad for that product type.

In [0]:
result = prod_log_cat.select('product_type', 'publication_url')
result = result.groupBy("product_type").agg(count('publication_url').alias('Count'), collect_list('publication_url').alias('Publication_URLs'))
result = result.orderBy(desc('Count'))
result.display()

product_type Count Publication_URLs computer 1449 List(https://www.nj.com, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.vox.com/, https://www.nbcnews.com/, https://www.engadget.com/, https://www.nydailynews.com/, https://www.mirror.co.uk/news/, https://www.businessinsider.com/, https://www.businessinsider.com/, https://www.telegraph.co.uk/, https://www.cnn.com/, https://www.vox.com/, https://www.cbsnews.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.latimes.com/, https://www.engadget.com/, https://www.bbc.com/, https://www.cnn.com/, https://abcnews.go.com/, https://www.telegraph.co.uk/, https://www.huffingtonpost.com/, https://www.huffingtonpost.com/, https://www.engadget.com/, https://www.telegraph.co.uk/, https://www.nydailynews.com/, https://www.nydailynews.com/, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.nj.com, https://www.telegraph.co.uk/, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.usnews.com/, https://www.usnews.com/, https://techcrunch.com/, https://techcrunch.com/, https://www.engadget.com/, https://www.usatoday.com/, https://www.cbsnews.com/, https://www.cnet.com/, https://www.buzzfeed.com/, https://www.buzzfeed.com/, https://www.bostonglobe.com/, https://www.bostonglobe.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.mirror.co.uk/news/, https://www.engadget.com/, https://nypost.com/, https://www.buzzfeed.com/, https://www.buzzfeed.com/, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.cbsnews.com/, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://nypost.com/, https://www.dallasnews.com/, https://www.usnews.com/, https://www.boston.com, https://www.engadget.com/, https://www.bbc.com/, https://www.dallasnews.com/, https://www.dallasnews.com/, https://www.boston.com, https://www.thedailybeast.com/, https://www.thedailybeast.com/, https://www.cnet.com/, https://www.telegraph.co.uk/, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://www.telegraph.co.uk/, https://www.telegraph.co.uk/, https://www.engadget.com/, https://www.boston.com, https://www.boston.com, https://www.bostonglobe.com/, https://www.bostonglobe.com/, https://www.examiner.com/, https://www.examiner.com/, https://abcnews.go.com/, https://techcrunch.com/, https://techcrunch.com/, https://www.thedailybeast.com/, https://www.thedailybeast.com/, https://www.nj.com, https://www.nj.com, https://abcnews.go.com/, https://www.salon.com/, https://www.cbsnews.com/, https://www.thedailybeast.com/, https://techcrunch.com/, https://techcrunch.com/, https://www.buzzfeed.com/, https://www.buzzfeed.com/, https://www.cbsnews.com/, https://www.cbsnews.com/, https://www.cnet.com/, https://www.engadget.com/, https://www.bostonglobe.com/, https://www.bostonglobe.com/, https://www.businessinsider.com/, https://www.businessinsider.com/, https://www.dailymail.co.uk/, https://www.dailymail.co.uk/, https://www.nytimes.com/, https://www.mirror.co.uk/news/, https://www.nytimes.com/, https://www.telegraph.co.uk/, https://www.buzzfeed.com/, https://www.usatoday.com/, https://www.upworthy.com/, https://www.huffingtonpost.com/, https://www.huffingtonpost.com/, https://abcnews.go.com/, https://www.thedailybeast.com/, https://www.boston.com, https://www.cbsnews.com/, https://www.al.com/, https://www.vox.com/, https://www.telegraph.co.uk/, https://www.nj.com, https://www.nj.com, https://www.msn.com/en-us/news, https://www.msn.com/en-us/news, https://nypost.com/, https://nypost.com/, https://www.latimes.com/, https://www.buzzfeed.com/, https://www.al.com/, https://nypost.com/, https://www.engadget.com/, https://www.al.com/, https://www.theatlantic.com/, https://abcnews.go.com/, https://www.telegraph.co.uk/, https://www.telegraph.co.uk/, https://www.examiner.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.examiner.com/, https://www.telegraph.co.uk/, https://www

### 3. For each product, compute the click rate for it.

In [0]:
result = prod_log_cat.select('product', 'click').filter(prod_log_cat.product.isNotNull())
result = result.groupBy("product").agg((sum('click')/count('click')).alias('click_rate'))
result = result.orderBy('product')
result = result.withColumn('click_rate', round('click_rate', 3))
result.display() 

product click_rate Apple computer 0.792 Apple iPad 0.502 Apple laptop 0.565 BasilBasel perfume 0.649 Broyhill recliner 0.539 Centrum MultiVitamins 0.627 Clinique moisturizer 0.806 Coach purse 0.389 Cougar jeans 0.26 Covergirl makeup 0.252 Dell computer 0.652 Dell laptop 0.315 Docker pants 0.684 Ford sedan 0.137 Gillette shaver 0.713 Giorgio perfume 0.799 Givenchy perfume 0.457 Guess perfume 0.407 Haier refrigerator 0.208 Hamilton Beach blender 0.408 Ikea sofa 0.573 InstantPot pressure cooker 0.5 Jaguar perfume 0.473 Kaai handbags 0.66 LG TV 0.481 LG dryer 0.63 LG washer 0.495 Lavazza Coffee 0.564 Lee jeans 0.467 Lenova laptop 0.637 Levis Jeans 0.668 Maybelline lipstick 0.561 Maytag dryer 0.345 Maytag refrigerator 0.397 Maytag washer 0.507 NemoK blender 0.57 NordicTrack elliptical 0.528 NordicTrack rower 0.223 NordicTrack treadmill 0.49 Remington shaver 0.35 Samsung TV 0.73 Samsung dryer 0.436 Samsung washer 0.553 Sony TV 0.393 Soundwave speakers 0.546 Starbucks Coffee 0.276 Tesla 0.592 Vitamix blender 0.507 bose speakers 0.526 covergirl lipstick 0.818

### 4. For each product, compute the click rate for each sentiment type

In [0]:
result = prod_log_cat.select('product','sentiment', 'click').filter(prod_log_cat.product.isNotNull())
result = result.groupBy("product","sentiment").agg((sum('click')/count('click')).alias('click_rate'))
result = result.orderBy('product', 'sentiment')
result = result.withColumn('click_rate', round('click_rate', 3))
result.display() 

product sentiment click_rate Apple computer negative 0.696 Apple computer neutral 0.923 Apple computer positive 0.765 Apple iPad negative 0.391 Apple iPad neutral 0.628 Apple iPad positive 0.494 Apple laptop negative 0.154 Apple laptop neutral 0.732 Apple laptop positive 0.773 BasilBasel perfume negative 0.771 BasilBasel perfume neutral 0.864 BasilBasel perfume positive 0.367 Broyhill recliner negative 0.814 Broyhill recliner neutral 0.563 Broyhill recliner positive 0.243 Centrum MultiVitamins negative 0.835 Centrum MultiVitamins neutral 0.815 Centrum MultiVitamins positive 0.187 Clinique moisturizer negative 0.903 Clinique moisturizer neutral 0.931 Clinique moisturizer positive 0.583 Coach purse negative 0.316 Coach purse neutral 0.453 Coach purse positive 0.4 Cougar jeans negative 0.083 Cougar jeans neutral 0.312 Cougar jeans positive 0.39 Covergirl makeup negative 0.113 Covergirl makeup neutral 0.385 Covergirl makeup positive 0.245 Dell computer negative 0.831 Dell computer neutral 0.382 Dell computer positive 0.72 Dell laptop negative 0.145 Dell laptop neutral 0.357 Dell laptop positive 0.453 Docker pants negative 0.836 Docker pants neutral 0.814 Docker pants positive 0.333 Ford sedan negative 0.013 Ford sedan neutral 0.125 Ford sedan positive 0.266 Gillette shaver negative 0.905 Gillette shaver neutral 0.961 Gillette shaver positive 0.14 Giorgio perfume negative 0.639 Giorgio perfume neutral 0.97 Giorgio perfume positive 0.831 Givenchy perfume negative 0.758 Givenchy perfume neutral 0.303 Givenchy perfume positive 0.338 Guess perfume negative 0.172 Guess perfume neutral 0.306 Guess perfume positive 0.788 Haier refrigerator negative 0.173 Haier refrigerator neutral 0.167 Haier refrigerator positive 0.283 Hamilton Beach blender negative 0.672 Hamilton Beach blender neutral 0.354 Hamilton Beach blender positive 0.216 Ikea sofa negative 0.84 Ikea sofa neutral 0.594 Ikea sofa positive 0.322 InstantPot pressure cooker negative 0.0 InstantPot pressure cooker neutral 0.864 InstantPot pressure cooker positive 0.714 Jaguar perfume negative 0.435 Jaguar perfume neutral 0.7 Jaguar perfume positive 0.311 Kaai handbags negative 0.491 Kaai handbags neutral 0.957 Kaai handbags positive 0.513 LG TV negative 0.299 LG TV neutral 0.591 LG TV positive 0.644 LG dryer negative 0.681 LG dryer neutral 0.792 LG dryer positive 0.395 LG washer negative 0.154 LG washer neutral 0.517 LG washer positive 0.829 Lavazza Coffee negative 0.841 Lavazza Coffee neutral 0.447 Lavazza Coffee positive 0.343 Lee jeans negative 0.342 Lee jeans neutral 0.778 Lee jeans positive 0.329 Lenova laptop negative 0.75 Lenova laptop neutral 0.714 Lenova laptop positive 0.419 Levis Jeans negative 0.405 Levis Jeans neutral 0.8 Levis Jeans positive 0.844 Maybelline lipstick negative 0.885 Maybelline lipstick neutral 0.21 Maybelline lipstick positive 0.698 Maytag dryer negative 0.118 Maytag dryer neutral 0.705 Maytag dryer positive 0.257 Maytag refrigerator negative 0.053 Maytag refrigerator neutral 0.722 Maytag refrigerator positive 0.429 Maytag washer negative 0.922 Maytag washer neutral 0.362 Maytag washer positive 0.279 NemoK blender negative 0.978 NemoK blender neutral 0.326 NemoK blender positive 0.317 NordicTrack elliptical negative 0.491 NordicTrack elliptical neutral 0.738 NordicTrack elliptical positive 0.345 NordicTrack rower negative 0.2 NordicTrack rower neutral 0.143 NordicTrack rower positive 0.297 NordicTrack treadmill negative 0.316 NordicTrack treadmill neutral 0.584 NordicTrack treadmill positive 0.56 Remington shaver negative 0.145 Remington shaver neutral 0.237 Remington shaver positive 0.744 Samsung TV negative 0.667 Samsung TV neutral 0.82 Samsung TV positive 0.703 Samsung dryer negative 0.276 Samsung dryer neutral 0.717 Samsung dryer positive 0.311 Samsung washer negative 0.0 Samsung washer neutral 0.707 Samsung washer positive 0.898 Sony TV negative 0.056 Sony TV neutral 0.679 Sony TV positive 0.431 Soundwave speakers negative 0.119 Soundwave speakers ne

### 5. For each product type, compute the click rate for it

In [0]:
result = prod_log_cat.select('product_type', 'click')
result = result.groupBy("product_type").agg((sum('click')/count('click')).alias('click_rate'))
result = result.orderBy('product_type')
result = result.withColumn('click_rate', round('click_rate', 3))
result.display() 

product_type click_rate null null blender 0.499 car 0.37 coffee 0.355 computer 0.5 dryer 0.453 elliptical trainer 0.528 face cream 0.806 furniture 0.555 jeans 0.451 lipstick 0.664 makeup 0.252 pants 0.684 perfume 0.566 pressure cooker 0.5 refrigerator 0.287 rowing machine 0.223 shaver 0.54 speakers 0.536 tablet 0.502 television 0.532 treadmill 0.49 vitamin 0.627 washer 0.52 women's purse 0.515

### 6. For each category, compute the click rate for it

In [0]:
result = prod_log_cat.select('category', 'click').filter(prod_log_cat.category.isNotNull())
result = result.groupBy("category").agg((sum('click')/count('click')).alias('click_rate'))
result = result.orderBy('category')
result = result.withColumn('click_rate', round('click_rate', 3))
result.display() 

category click_rate accessories 0.515 apparel 0.493 beauty products 0.58 consumer electronics 0.514 fitness equipment 0.418 footwear null health 0.627 household durables 0.555 large kitchen appliances 0.456 packaged food 0.355 small kitchen appliances 0.499 transportation 0.37

### 7. For each product type, compute the click rate for each sentiment type

In [0]:
result = prod_log_cat.select('product_type','sentiment', 'click')
result = result.groupBy("product_type","sentiment").agg((sum('click')/count('click')).alias('click_rate'))
result = result.orderBy('product_type', 'sentiment')
result = result.withColumn('click_rate', round('click_rate', 3))
result.display() 

product_type sentiment click_rate null null null blender negative 0.743 blender neutral 0.338 blender positive 0.379 car negative 0.392 car neutral 0.582 car positive 0.157 coffee negative 0.465 coffee neutral 0.357 coffee positive 0.241 computer negative 0.414 computer neutral 0.516 computer positive 0.571 dryer negative 0.324 dryer neutral 0.735 dryer positive 0.309 elliptical trainer negative 0.491 elliptical trainer neutral 0.738 elliptical trainer positive 0.345 face cream negative 0.903 face cream neutral 0.931 face cream positive 0.583 furniture negative 0.825 furniture neutral 0.579 furniture positive 0.279 jeans negative 0.265 jeans neutral 0.61 jeans positive 0.51 lipstick negative 0.692 lipstick neutral 0.504 lipstick positive 0.826 makeup negative 0.113 makeup neutral 0.385 makeup positive 0.245 pants negative 0.836 pants neutral 0.814 pants positive 0.333 perfume negative 0.556 perfume neutral 0.611 perfume positive 0.531 pressure cooker negative 0.0 pressure cooker neutral 0.864 pressure cooker positive 0.714 refrigerator negative 0.122 refrigerator neutral 0.389 refrigerator positive 0.347 rowing machine negative 0.2 rowing machine neutral 0.143 rowing machine positive 0.297 shaver negative 0.528 shaver neutral 0.652 shaver positive 0.442 speakers negative 0.349 speakers neutral 0.706 speakers positive 0.543 tablet negative 0.391 tablet neutral 0.628 tablet positive 0.494 television negative 0.319 television neutral 0.7 television positive 0.593 treadmill negative 0.316 treadmill neutral 0.584 treadmill positive 0.56 vitamin negative 0.835 vitamin neutral 0.815 vitamin positive 0.187 washer negative 0.377 washer neutral 0.521 washer positive 0.647 women's purse negative 0.386 women's purse neutral 0.694 women's purse positive 0.458

### Question 8
Choose a product. Determine if there are any ‘significant’ differences in the correlation between
the sentiment type of the ad context and clicking on the product type conditioned on gender. Let
us consider 7% difference between the highest click rate and the second highest click rate is our
criterion of significance. The example below illustrates what I mean.
Say the average click rate for blenders is 0.3 for females when the context is positive, 0.2 for
females when the context is neutral and 0.1 when the context is negative. Turning these figure into
percentages gets us :
  female, pos: 0.3/0.6 = 50%
  female, neut: 0.2/0.6 = 33%
  female, neg: 0.1/0.6 = 17%
This means that the correlation the sentiment type of the context of the ads for blenders is
significant for females. I.e., females are much more likely to click on an ad for blenders when the context
is positive. Compute these figures for all 3 genders. Try to choose a product type for which the difference is significant for all 3 genders. Keep in mind the ads for specific products, not product types.

In [0]:
# 8 
from pyspark.sql.window import Window
# Pull the required fields
result = prod_log_cat.select('product_type','gender','sentiment','click')
# .filter(prod_log_cat.click.isNotNull())

# Calculate the average click rate
result = result.groupBy("product_type", 'gender','sentiment').agg(sum("click").alias("clicks"), count("click").alias("total"))\
    .withColumn("avg_click_rate", col("clicks") / col("total"))
result = result.orderBy('product_type', 'sentiment', 'gender') 

# Calculate the share (for example, for females, it would be the sum of avg_click_rate for each sentiment)
result = result.withColumn('share',  sum('avg_click_rate').over(Window.partitionBy('product_type', 'gender').orderBy('sentiment') 
                            .rowsBetween(Window.unboundedPreceding, Window.unboundedFollowing))) 

result = result.withColumn('correlation_pct', (col('avg_click_rate')/col('share'))*100) 

# Find the highest and second highest click rates
result = result.withColumn('rank', row_number().over(Window.partitionBy('product_type', 'gender').orderBy(desc('avg_click_rate'))))
result = result.withColumn('highest',  max('correlation_pct').over(Window.partitionBy('product_type', 'gender').orderBy('sentiment') 
                            .rowsBetween(Window.unboundedPreceding, Window.unboundedFollowing))) 
result = result.withColumn('second_highest', when(col("rank") == 2, col('correlation_pct')).otherwise(None))
result = result.withColumn('second_highest',max('second_highest').over(Window.partitionBy( "product_type", "gender")))

# Are the differences significant?
result = result.withColumn('significance', (col('highest')-col('second_highest')))
result = result.withColumn('check', when(col('significance') > 7, True).otherwise(False))

# Formatting numerical values
result = result.withColumn('avg_click_rate', round('avg_click_rate', 3))\
    .withColumn('share', round('share', 3)).withColumn('correlation_pct', round('correlation_pct', 2))\
    .withColumn('highest', round('highest', 3)).withColumn('second_highest', round('second_highest', 3))\
    .withColumn('significance', round('significance', 3)) 

result = result.filter(col("rank")==1)

# Final result
all_product_types = result.select('product_type').distinct().rdd.flatMap(lambda x: x).collect()

# Iterate through each product type
for target_product_type in all_product_types:
    # Filter the results for the specified product type and where 'check' is True
    filtered_results = result.filter((col('product_type') == target_product_type) & (col('check') == True))

    # Check if all three genders are present for the specified product type
    distinct_genders = filtered_results.select('gender').distinct().rdd.flatMap(lambda x: x).collect()

    if set(distinct_genders) == {"male", "female", "non-binary"}:
        # Display the results if all three genders are present
        filtered_results.select("product_type", "gender", "sentiment", "clicks", "total", "avg_click_rate", "share", "correlation_pct", "significance", "check").display()
        continue
    else:
        print(f"All three genders are not present for the product type {target_product_type}.")

# If no product type meets the criteria
else:
    print("No product type found with all three genders.")

All three genders are not present for the product type television.
All three genders are not present for the product type refrigerator.
All three genders are not present for the product type lipstick.
All three genders are not present for the product type face cream.
All three genders are not present for the product type vitamin.
All three genders are not present for the product type None.
All three genders are not present for the product type tablet.
All three genders are not present for the product type rowing machine.
All three genders are not present for the product type pressure cooker.
All three genders are not present for the product type shaver.


product_type gender sentiment clicks total avg_click_rate share correlation_pct significance check washer female positive 95.0 148 0.642 1.52 42.22 8.756 true washer male positive 85.0 129 0.659 1.57 41.96 8.031 true washer non-binary negative 1.0 1 1.0 1.0 100.0 100.0 true

All three genders are not present for the product type makeup.
All three genders are not present for the product type women's purse.
All three genders are not present for the product type jeans.
All three genders are not present for the product type furniture.
All three genders are not present for the product type dryer.
All three genders are not present for the product type elliptical trainer.
All three genders are not present for the product type coffee.
All three genders are not present for the product type computer.
All three genders are not present for the product type speakers.
All three genders are not present for the product type car.
All three genders are not present for the product type treadmill.
All three genders are not present for the product type perfume.
All three genders are not present for the product type blender.
All three genders are not present for the product type pants.
No product type found with all three genders.


### 9. For extra-credit do the same analysis as in question 8 with gender replaced by age-group.

In [0]:
# 9
from pyspark.sql.window import Window
# Pull the required fields
result = prod_log_cat.select('product_type','age_group','sentiment','click').filter(prod_log_cat.click.isNotNull())

# Calculate the average click rate
result = result.groupBy("product_type", 'age_group','sentiment').agg(sum("click").alias("clicks"), count("click").alias("total"))\
    .withColumn("avg_click_rate", col("clicks") / col("total"))
result = result.orderBy('product_type', 'sentiment', 'age_group') 

# Calculate the share (for example, for females, it would be the sum of avg_click_rate for each sentiment)
result = result.withColumn('share',  sum('avg_click_rate').over(Window.partitionBy('product_type', 'age_group').orderBy('sentiment') 
                            .rowsBetween(Window.unboundedPreceding, Window.unboundedFollowing))) 

result = result.withColumn('correlation_pct', (col('avg_click_rate')/col('share'))*100)

# Find the highest and second highest click rates
result = result.withColumn('rank', row_number().over(Window.partitionBy('product_type', 'age_group').orderBy(desc('avg_click_rate'))))
result = result.withColumn('highest',  max('correlation_pct').over(Window.partitionBy('product_type', 'age_group').orderBy('sentiment') 
                            .rowsBetween(Window.unboundedPreceding, Window.unboundedFollowing))) 
result = result.withColumn('second_highest', when(col("rank") == 2, col('correlation_pct')).otherwise(None))
result = result.withColumn('second_highest',max('second_highest').over(Window.partitionBy( "product_type", "age_group")))

# Are the differences significant?
result = result.withColumn('significance', (col('highest')-col('second_highest')))
result = result.withColumn('check', when(col('significance') > 7, "yes").otherwise("no"))

# Formatting numerical values
result = result.withColumn('avg_click_rate', round('avg_click_rate', 3))\
    .withColumn('share', round('share', 3)).withColumn('correlation_pct', round('correlation_pct', 2))\
    .withColumn('highest', round('highest', 3)).withColumn('second_highest', round('second_highest', 3))\
    .withColumn('significance', round('significance', 3)) 

result = result.filter(col("rank")==1)

# Final result
for target_product_type in all_product_types:
    # Filter the results for the specified product type and where 'check' is True
    filtered_results = result.filter((col('product_type') == target_product_type) & (col('check') == True))

    # Check if all age groups are present for the specified product type
    distinct_age_group = filtered_results.select('age_group').distinct().rdd.flatMap(lambda x: x).collect()

    if set(distinct_age_group) == {"juvenile", "middle-age", "senior", "young"}:
        # Display the results if all age groups are present
        filtered_results.select("product_type", "age_group", "sentiment", "clicks", "total", "avg_click_rate", "share", "correlation_pct", "significance", "check").display()
        continue  
    else:
        print(f"All age-groups are not present for the product type {target_product_type}.")

# If no product type meets the criteria
else:
    print("No product type found with all age-groups.")

All age-groups are not present for the product type television.
All age-groups are not present for the product type refrigerator.
All age-groups are not present for the product type lipstick.
All age-groups are not present for the product type face cream.
All age-groups are not present for the product type vitamin.
All age-groups are not present for the product type None.
All age-groups are not present for the product type tablet.


product_type age_group sentiment clicks total avg_click_rate share correlation_pct significance check rowing machine juvenile negative 4.0 21 0.19 0.24 79.21 58.416 yes rowing machine middle-age positive 9.0 22 0.409 0.636 64.37 36.601 yes rowing machine senior negative 4.0 12 0.333 0.694 48.0 12.0 yes rowing machine young positive 10.0 14 0.714 1.19 60.0 32.0 yes

All age-groups are not present for the product type pressure cooker.
All age-groups are not present for the product type shaver.
All age-groups are not present for the product type washer.
All age-groups are not present for the product type makeup.
All age-groups are not present for the product type women's purse.
All age-groups are not present for the product type jeans.
All age-groups are not present for the product type furniture.


product_type age_group sentiment clicks total avg_click_rate share correlation_pct significance check dryer juvenile neutral 38.0 51 0.745 1.385 53.81 28.536 yes dryer middle-age neutral 29.0 42 0.69 1.137 60.75 37.286 yes dryer senior neutral 27.0 36 0.75 1.383 54.25 28.931 yes dryer young neutral 25.0 33 0.758 1.561 48.53 19.413 yes

All age-groups are not present for the product type elliptical trainer.
All age-groups are not present for the product type coffee.
All age-groups are not present for the product type computer.
All age-groups are not present for the product type speakers.


product_type age_group sentiment clicks total avg_click_rate share correlation_pct significance check car juvenile neutral 20.0 35 0.571 1.004 56.93 18.836 yes car middle-age neutral 16.0 33 0.485 0.996 48.68 8.041 yes car senior neutral 31.0 43 0.721 1.46 49.37 20.837 yes car young neutral 22.0 42 0.524 1.072 48.84 15.171 yes

All age-groups are not present for the product type treadmill.
All age-groups are not present for the product type perfume.


product_type age_group sentiment clicks total avg_click_rate share correlation_pct significance check blender juvenile negative 45.0 60 0.75 1.384 54.2 31.076 yes blender middle-age negative 48.0 65 0.738 1.336 55.26 32.811 yes blender senior negative 37.0 55 0.673 1.519 44.27 16.068 yes blender young negative 49.0 61 0.803 1.581 50.79 21.609 yes

All age-groups are not present for the product type pants.
No product type found with all age-groups.
